In [16]:
import pandas as pd
import json
from collections import defaultdict
import pickle

In [ ]:
## The notebook shows how we parsed wqsp and created dataset for training T5. The output file is already provided in Data

In [24]:
def cleanprop(p):
    topic, sub = p.rsplit('.', 1)
    _, topic = topic.rsplit('.', 1)
    sub = sub.replace('_', ' ')
    topic = topic.replace('_', ' ')
    return topic, sub

In [6]:
gold_train = json.loads(open('data/WebQSP.train.json').read())
prop_train = defaultdict(list)
for i in gold_train['Questions']:
    P = i['Parses'][0]
    if P['TopicEntityName'] == None:
        continue
    if P['InferentialChain']:
        props = P['InferentialChain']
        ans = []
        for a in P['Answers']:
            if a['AnswerType'] == "Value":
                ans.append(a['AnswerArgument'].lower())
            else:
                ans.append(a['EntityName'].lower())
        if len(props) ==1:
            p = props[0]
            prop_train[p].append((P['TopicEntityName'].lower(), i['RawQuestion'].lower(), ans))
len(prop_train)

220

In [5]:
gold_train

{'Version': '1.0',
 'FreebaseVersion': '2015-08-09',
 'Questions': [{'QuestionId': 'WebQTrn-0',
   'RawQuestion': 'what is the name of justin bieber brother?',
   'ProcessedQuestion': 'what is the name of justin bieber brother',
   'Parses': [{'ParseId': 'WebQTrn-0.P0',
     'AnnotatorId': 1,
     'AnnotatorComment': {'ParseQuality': 'Complete',
      'QuestionQuality': 'Good',
      'Confidence': 'Normal',
      'FreeFormComment': 'First-round parse verification'},
     'Sparql': "PREFIX ns: <http://rdf.freebase.com/ns/>\nSELECT DISTINCT ?x\nWHERE {\nFILTER (?x != ns:m.06w2sn5)\nFILTER (!isLiteral(?x) OR lang(?x) = '' OR langMatches(lang(?x), 'en'))\nns:m.06w2sn5 ns:people.person.sibling_s ?y .\n?y ns:people.sibling_relationship.sibling ?x .\n?x ns:people.person.gender ns:m.05zppz .\n}\n",
     'PotentialTopicEntityMention': 'justin bieber',
     'TopicEntityName': 'Justin Bieber',
     'TopicEntityMid': 'm.06w2sn5',
     'InferentialChain': ['people.person.sibling_s',
      'people.s

In [17]:
'ice_hockey.hockey_team.coach' in prop_train

True

In [11]:
prop_train

defaultdict(list,
            {'location.location.containedby': [('grand bahama',
               'what country is the grand bahama island in?',
               ['bahamas']),
              ('rome',
               'where is rome italy located on a map?',
               ['italy', 'lazio', 'province of rome']),
              ('netherlands',
               'where are the netherlands on a world map?',
               ['kingdom of the netherlands']),
              ('london heathrow airport',
               'what county is heathrow airport in?',
               ['hillingdon']),
              ('santa clara university',
               'where is santa clara university?',
               ['california', 'united states of america', 'santa clara']),
              ('river thames',
               'where is the thames river located?',
               ['europe', 'england', 'united kingdom']),
              ('whistler mountain',
               'where is whistler mountain located?',
               ['british col

In [17]:
gold_test = json.loads(open('data/WebQSP.test.json').read())
prop_test = defaultdict(list)
for i in gold_test['Questions']:
    P = i['Parses'][0]
    if P['TopicEntityName'] == None:
        continue
    if P['InferentialChain']:
        props = P['InferentialChain']
        ans = []
        for a in P['Answers']:
            if a['AnswerType'] == "Value":
                ans.append(a['AnswerArgument'].lower())
            else:
                ans.append(a['EntityName'].lower())
        if len(props) ==1:
            p = props[0]
            prop_test[p].append((P['TopicEntityName'].lower(), i['RawQuestion'].lower(), ans))
len(prop_test)

160

In [18]:
ptrn = set(prop_train.keys())
ptst = set(prop_test.keys())

In [19]:
unseen = ptst - ptrn
seen = set.intersection(ptst , ptrn)
unio = set.union(ptst, ptrn)

In [20]:
with open('data/seen.pkl', 'wb') as f:
    pickle.dump(seen, f)

In [21]:
with open('data/unseen.pkl', 'wb') as f:
    pickle.dump(unseen, f)

In [22]:
with open('data/unio.pkl', 'wb') as f:
    pickle.dump(unio, f)

In [23]:
train_list = []
for p in ptrn:
    topic, sub = cleanprop(p)
    for i in prop_train[p]:
        head, q, ans = i
        for a in ans:
            #print(head)
            #print(topic)
            #print(sub)
            #print(a)
            #print(q)
            #print(p)
            #print()
            train_list.append((head, topic, sub, a, q, p))

AttributeError: 'int' object has no attribute 'rsplit'

In [81]:
df=pd.DataFrame(train_list, columns=['head', 'topic', 'sub', 'ans', 'target_text', 'prop']).drop_duplicates().dropna()
df.to_csv('data/data_train_t5.csv')

In [112]:
## Now generating subsets from the TEST data
test_list_seen = []
for p in seen:
    topic, sub = cleanprop(p)
    for i in prop_test[p]:
        head, q, ans = i
        for a in ans:
            #print(head)
            #print(topic)
            #print(sub)
            #print(a)
            #print(q)
            #print(p)
            #print()
            test_list_seen.append((q, p))

In [113]:
df=pd.DataFrame(test_list_seen, columns=['QA', 'Rel']).drop_duplicates().dropna()
df.to_csv('data/data_test_seen.csv')
len(df)

986

In [120]:
## Now generating subsets from the TEST data
test_list_unseen = []
for p in unseen:
    topic, sub = cleanprop(p)
    for i in prop_test[p]:
        head, q, ans = i
        for a in ans:
            #print(head)
            #print(topic)
            #print(sub)
            #print(a)
            #print(q)
            #print(p)
            #print()
            test_list_unseen.append((q, p))

In [121]:
df=pd.DataFrame(test_list_unseen, columns=['QA', 'Rel']).drop_duplicates().dropna()
df.to_csv('data/data_test_unseen.csv')
len(df)

43